# ccache

In [1]:
import shutil
from pathlib import Path
import tempfile
import tvm
from tvm.contrib.cc import create_shared, create_executable, _is_linux_like, _is_windows_like

In [2]:
def _src_gen(text):
    return """
#include <iostream>

int main() {
    std::cout << "text";
    return 0;
}""".replace(
        "text", text
    )

In [3]:
def _compile(f_create, text, output):
    with tempfile.TemporaryDirectory() as temp_dir:
        temp_dir = Path(temp_dir)
        src_path = temp_dir/"src.cpp"
        with open(src_path, "w", encoding="utf-8") as file:
            file.write(_src_gen(text))
        log_path = temp_dir/"log.txt"
        ccache_env = {
            "CCACHE_COMPILERCHECK": "content",
            "CCACHE_LOGFILE": log_path,
        }
        f_create(output, ["src.cpp"], ["-c"], cwd=temp_dir, ccache_env=ccache_env)
        with open(log_path, "r", encoding="utf-8") as file:
            log = file.read()
        return log

In [4]:
shutil.which("ccache") # 查看安装位置

'/usr/bin/ccache'

## 测试共享

In [5]:
if _is_linux_like():
    _ = _compile(create_shared, "shared", "main.o")
    log = _compile(create_shared, "shared", "main.o")
    assert "Succeeded getting cached result" in log
elif _is_windows_like():
    _ = _compile(create_shared, "shared", "main.obj")
    log = _compile(create_shared, "shared", "main.obj")
    assert "Succeeded getting cached result" in log

In [6]:
print(log)

[2025-05-16T15:27:35.389101 995845] === CCACHE 3.7.7 STARTED =========================================
[2025-05-16T15:27:35.389101 995845] Config: (default) base_dir = 
[2025-05-16T15:27:35.389101 995845] Config: (default) cache_dir = /home/ai/.ccache
[2025-05-16T15:27:35.389101 995845] Config: (default) cache_dir_levels = 2
[2025-05-16T15:27:35.389101 995845] Config: (default) compiler = 
[2025-05-16T15:27:35.389101 995845] Config: (environment) compiler_check = content
[2025-05-16T15:27:35.389101 995845] Config: (default) compression = false
[2025-05-16T15:27:35.389101 995845] Config: (default) compression_level = 6
[2025-05-16T15:27:35.389101 995845] Config: (default) cpp_extension = 
[2025-05-16T15:27:35.389101 995845] Config: (default) debug = false
[2025-05-16T15:27:35.389101 995845] Config: (default) depend_mode = false
[2025-05-16T15:27:35.389101 995845] Config: (default) direct_mode = true
[2025-05-16T15:27:35.389101 995845] Config: (default) disable = false
[2025-05-16T15:27:

## 测试 executable

In [7]:
if _is_linux_like():
    _ = _compile(create_executable, "executable", "main")
    log = _compile(create_executable, "executable", "main")
    assert "Succeeded getting cached result" in log
elif _is_windows_like():
    _ = _compile(create_executable, "executable", "main.exe")
    log = _compile(create_executable, "executable", "main.exe")
    assert "Succeeded getting cached result" in log